In [19]:
import os
import sys
import math
import json
from typing import List, Dict, Optional, Tuple

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt


from sklearn.cluster import DBSCAN
from sklearn.preprocessing import StandardScaler
import plotly.express as px

In [20]:
df = pd.read_csv("Data/CrashStatisticsFranklinCounty.csv")

C:\Users\raab.75\AppData\Local\Temp\ipykernel_30348\1550891691.py:1: DtypeWarning: Columns (23,31) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("Data/CrashStatisticsFranklinCounty.csv")


In [9]:
df

LocalReportNumber  DocumentNumber         CrashSeverity   HitSkip  \
0             \t20183624     20202168971                 Fatal       NaN   
1             \t20179633     20202168999                 Fatal       NaN   
2             \t20179416     20202172825                 Fatal       NaN   
3             \t20193278     20202183697                 Fatal  Unsolved   
4             \t20214201     20202206898                 Fatal       NaN   
...                  ...             ...                   ...       ...   
115676       \t202501180     20258172808  Property Damage Only       NaN   
115677  \t25whi-22254-AC     20258173076  Property Damage Only       NaN   
115678  \t25WHI-22233-AC     20258173087       Injury Possible       NaN   
115679  \t25WHI-21784-AC     20258173091  Property Damage Only  Unsolved   
115680  \t25WHI-21950-AC     20258173093  Property Damage Only       NaN   

       LocalInformation  SecondaryCrash  PhotosTaken    OH2    OH3   OH1P  \
0                   NaN           False         True   True   True   True   
1                   NaN           False        False   True  False   True   
2                   NaN           False         True   True  False  False   
3                   NaN           False         True   True   True  False   
4                   NaN           False         True  False  False  False   
...                 ...             ...          ...    ...    ...    ...   
115676              NaN           False         True   True  False  False   
115677              NaN           False        False  False  False  False   
115678              NaN           False         True  False  False  False   
115679              NaN           False         True  False  False  False   
115680              NaN           False         True   True   True  False   

        ...  PedestrianRelated  SemiTruckRelated SmallTruckRelated  \
0       ...               True             False              True   
1       ...              False              True              True   
2       ...              False             False              True   
3       ...               True             False             False   
4       ...              False             False             False   
...     ...                ...               ...               ...   
115676  ...              False             False             False   
115677  ...              False             False             False   
115678  ...              False             False             False   
115679  ...              False             False             False   
115680  ...              False             False             False   

        YouthRelated  TeenRelated DUI21Related SeniorRelated  \
0              False        False        False         False   
1              False        False        False          True   
2               True        False        False         False   
3              False        False        False          True   
4              False        False        False         False   
...              ...          ...          ...           ...   
115676         False        False        False         False   
115677         False        False        False         False   
115678         False        False        False         False   
115679         False        False        False         False   
115680          True         True        False         False   

       FatalNotReportable CommercialRelated  CommercialAtFault  
0                   False             False              False  
1                   False              True               True  
2                   False             False              False  
3                   False             False              False  
4                   False             False              False  
...                   ...               ...                ...  
115676              False             False              False  
115677              False             F

In [21]:
# Check how many duplicate rows exist
# we do not seem to have duplicates, nice
num_duplicates = df.duplicated().sum()
print(f"Number of duplicate rows: {num_duplicates}")

Number of duplicate rows: 0


In [22]:
'''
issue: we have about 850 rows where the coordinates are Nan, but location can be backtraced using 

Latitude
Longitude
LocationRouteType
LocationRouteNumber
LocationPrefix
LocationRoadName
LocationRoadType
DistanceFromReference
DistanceReferenceMeasurement
DirectionFromReference
ReferenceRouteType
ReferenceRouteNumber
ReferencePrefix
ReferenceName
ReferencePointUsed
ReferenceRoadType

However, out of 115681 total data points in Franklin County, this is less than 1%, so, we shall drop those lines
'''

# Count NaNs in specific columns
nan_counts = df[["Latitude", "Longitude"]].isna().sum()
print(nan_counts)

# Select rows with missing coordinates
missing_coords = df[df["Latitude"].isna() | df["Longitude"].isna()]

# Print the first 5 rows
columns_to_show = ["Latitude", "Longitude", "LocationRouteType", "LocationRouteNumber", "LocationPrefix", "LocationRoadName", "ReferenceName", "ReferencePointUsed", "DistanceReferenceMeasurement"]
print(missing_coords[columns_to_show].head(5))  # first 10 rows


# here we drop all rows that contain no coordinate info
df= df.dropna(subset=["Latitude", "Longitude"])


Latitude     839
Longitude    850
dtype: int64
      Latitude  Longitude LocationRouteType LocationRouteNumber  \
4408       NaN        NaN               NaN                 NaN   
4447       NaN        NaN       State Route                 161   
4573       NaN        NaN               NaN                 NaN   
4619       NaN        NaN               NaN                 NaN   
4649       NaN        NaN               NaN                 NaN   

     LocationPrefix LocationRoadName ReferenceName ReferencePointUsed  \
4408            NaN       STRINGTOWN           NaN       Intersection   
4447            NaN              NaN      EITERMAN       Intersection   
4573            NaN         COMODITY       LASALLE       Intersection   
4619            NaN       STRINGTOWN      MCDOWELL       Intersection   
4649           West          SCHROCK            55       House Number   

     DistanceReferenceMeasurement  
4408                         Feet  
4447                        Yards  
457

In [33]:
# Convert longitude and latitute to radians
coords = np.radians(df[["Latitude", "Longitude"]].values)

kms_per_radian = 6371.0088
epsilon = 0.01 / kms_per_radian   # 20 m in km, converted to radians

db = DBSCAN(eps=epsilon, min_samples=1, algorithm="ball_tree", metric="haversine").fit(coords)
df["cluster"] = db.labels_

# Aggregate crashes by cluster
clustered = df.groupby("cluster").agg({
    "Latitude": "mean",
    "Longitude": "mean",
    "cluster": "count"
}).rename(columns={"cluster": "count"}).reset_index(drop=True)

# Plot clusters on a map
fig = px.scatter_map(
    clustered,
    lat="Latitude", lon="Longitude",
    size="count", color="count",
    size_max=20, zoom=9,
    map_style="carto-positron"
)
fig.show()

In [ ]:
#there are some strange very large clusters on that map, but that might be a representation issue. Problem for later, zooming in on map gives a reasonable picture

max_count = clustered["count"].max()
largest_clusters = clustered[clustered["count"] == max_count]

print("Largest cluster(s):")
print(largest_clusters)

largest_cluster_ids = df.loc[df["cluster"].isin(largest_clusters.index), "cluster"]

largest_rows = df[df["cluster"].isin(largest_cluster_ids)]

#
#some additional large cluster info 
location_cols = [
    "LocationRouteType",
    "LocationRouteNumber",
    "LocationPrefix",
    "LocationRoadName",
    "LocationRoadType",
    "DistanceFromReference",
    "DistanceReferenceMeasurement",
    "DirectionFromReference",
    "ReferenceRouteType",
    "ReferenceRouteNumber",
    "ReferencePrefix",
    "ReferenceName",
    "ReferencePointUsed",
    "ReferenceRoadType"
]

print(largest_rows[location_cols].drop_duplicates())

Largest cluster(s):
       Latitude  Longitude  count
3660  40.099587 -83.109123    203
       LocationRouteType LocationRouteNumber LocationPrefix  LocationRoadName  \
4424         State Route                 161            NaN               NaN   
4518    Federal US Route                  33            NaN               NaN   
4759    Federal US Route                  33            NaN               NaN   
4877         State Route                  33            NaN               NaN   
4920         State Route                 257            NaN               NaN   
5576                 NaN                 NaN            NaN         RIVERSIDE   
24076        State Route                 161            NaN               NaN   
24495                NaN                 NaN           West  DUBLIN-GRANVILLE   
26290        State Route                 257            NaN               NaN   
26904        State Route                 161            NaN               NaN   
28945        State Ro